In [ ]:
# data = "data/data-3d9Ex.csv"
import plotly.express as px
import pandas as pd
import geopandas as gpd
import numpy as np
import json

colorscales = px.colors.named_colorscales()

In [ ]:
# Hungary counties shapefile
url = "https://maps.princeton.edu/download/file/stanford-dt251rh6351-shapefile.zip"

In [ ]:
#!cd data && wget https://maps.princeton.edu/download/file/stanford-dt251rh6351-shapefile.zip  && unzip stanford-dt251rh6351-shapefile.zip

In [ ]:
# read shp data into geopandas
gg = gpd.read_file("data/dt251rh6351.shp")
ggjson = gg.to_json()
gg.head()

In [ ]:
gg.iloc[1].geometry

In [ ]:
# We will need gejson
dggjson = json.loads(ggjson)

In [ ]:
# Turns out one of the county's name is misspelled so we rename it for now in the dataframe
[f['properties']['name_1'] for f in dggjson['features']]

## Heti adatok

### Letoltes
https://atlo.team/koronaterkep/#megyeibovebb

In [ ]:
# https://www.eea.europa.eu/data-and-maps/data/eea-reference-grids-2/gis-files/hungary-shapefile
url = "https://docs.google.com/spreadsheets/d/1djH-yUHLPwuEExCjiXS__6-8W2Yp_msFvShpL4bBcuM/export?format=xlsx&gid=1283792994"
heti_df = pd.read_excel(url)         

heti_df['date'] = pd.to_datetime(heti_df['Dátum']) #, format='%y-%m-%d')
heti_df = heti_df.drop(columns=['Dátum', 'Összesen'])

In [ ]:
heti_df.head(7)

In [ ]:
#Rename Győr to Gyor
heti_df = heti_df.rename(columns={'Győr-Moson-Sopron':'Gyor-Moson-Sopron'})

In [ ]:
import datetime as dt

In [ ]:
start_date = heti_df.loc[0,'date']
end_date = start_date + dt.timedelta(days=7)

mask = (heti_df['date'] >= start_date) & (heti_df['date'] < end_date)

hhdf = heti_df.loc[mask].drop(columns=['date']).transpose()

In [ ]:
hhdf['sum'] = hhdf.sum(axis=1)
hhdf = hhdf.reset_index().rename(columns={'index':'name_1'})

In [ ]:
hhdf

In [ ]:
# Get the mean of the county's centroids
cc = gg.centroid

clon = cc.apply(lambda x: x.x).mean()
clat = cc.apply(lambda x: x.y).mean()

In [ ]:
fig = px.choropleth_mapbox(hhdf.drop(columns=[0,1,2,3,4,5,6]), geojson=dggjson, locations='name_1', color='sum',
                           color_continuous_scale="Viridis",
                           #locationmode='geojson-id',
                    featureidkey='properties.name_1',
                           range_color=(0, 1800),
                           mapbox_style="carto-positron",
                           zoom=5.7, center = {"lat": clat, "lon": clon},
                           opacity=0.5,
                           labels={'sum':'Megfertozodesek szama'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()


In [ ]:
thhdf = hhdf.drop(columns=[0,1,2,3,4,5,6])

## Using the built-in plotly choropleth maps
This is not very decorative

In [ ]:
fig = px.choropleth(thhdf, geojson=dggjson, locations='name_1',#, color='sum',
                       color_continuous_scale="Viridis",
                           range_color=(0, 1800),
                        locationmode='geojson-id',
                    featureidkey='properties.name_1',
                    color=thhdf['sum'],
                           labels={'sum' : 'Megfertozodesek szama'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l": 0,"b":0}, geo_scope='europe'
                 )
fig.layout.geo.center.lat = clat
fig.layout.geo.center.lon = clon
fig.layout.geo.projection.scale = 9
fig.show()
